In [1]:
import pickle
embeddings = {}
with open('data/commonvoice_embeddings.pkl', 'rb') as file:
    embeddings = pickle.load(file)
embeddings

{'common_voice_en_41910645': array([-3.15453298e-02, -3.35898879e-03, -5.56861497e-02, -8.31159428e-02,
         6.88949302e-02, -7.28212520e-02,  1.02878384e-01, -2.67027058e-02,
         1.82280734e-01, -2.28066772e-01,  2.66924724e-02,  3.41618918e-02,
         4.58856523e-02,  2.45127063e-02,  1.03534371e-01, -5.99884018e-02,
        -4.79441822e-01,  3.26597422e-01,  2.87402179e-02,  8.89797807e-02,
        -2.03458562e-01,  6.39795437e-02,  4.14546162e-01,  8.51472467e-03,
         7.71588311e-02,  1.47171346e-02, -6.78148806e-01,  1.19423186e-02,
        -4.88879122e-02, -2.17297748e-01,  1.92979202e-01, -7.21347611e-03,
        -1.46038001e-02, -1.25812009e-01, -1.18377417e-01,  1.35955736e-01,
        -4.48507927e-02, -1.38092324e-01, -9.13960710e-02,  1.51570424e-01,
        -1.36539310e-01, -1.08446635e-01, -1.61561772e-01,  1.71825632e-01,
        -2.79764622e-01, -5.54961525e-03, -1.56598184e-02,  4.08770666e-02,
         1.28298044e-01,  2.16035396e-02, -6.90517575e-02,  

In [2]:
import pandas as pd
df = pd.read_csv("./data/cv-corpus-21.0-delta-2025-03-14/en/validated.tsv", delimiter="\t")
value_dict = df[["path", "gender"]]
value_dict = value_dict.set_index("path").rename_axis(None)
value_dict = value_dict.to_dict()["gender"]
value_dict

{'common_voice_en_41923025.mp3': nan,
 'common_voice_en_42356358.mp3': nan,
 'common_voice_en_42165090.mp3': nan,
 'common_voice_en_41921729.mp3': nan,
 'common_voice_en_42528393.mp3': nan,
 'common_voice_en_42006138.mp3': nan,
 'common_voice_en_42555516.mp3': nan,
 'common_voice_en_41951792.mp3': nan,
 'common_voice_en_42446785.mp3': nan,
 'common_voice_en_41974998.mp3': nan,
 'common_voice_en_42020013.mp3': nan,
 'common_voice_en_42046273.mp3': nan,
 'common_voice_en_42458975.mp3': nan,
 'common_voice_en_42494012.mp3': nan,
 'common_voice_en_42435518.mp3': nan,
 'common_voice_en_41930868.mp3': nan,
 'common_voice_en_42251480.mp3': 'male_masculine',
 'common_voice_en_41923270.mp3': nan,
 'common_voice_en_42594358.mp3': 'female_feminine',
 'common_voice_en_42141720.mp3': nan,
 'common_voice_en_42498572.mp3': nan,
 'common_voice_en_42216083.mp3': 'male_masculine',
 'common_voice_en_42466107.mp3': 'female_feminine',
 'common_voice_en_41970688.mp3': nan,
 'common_voice_en_42437221.mp3': n

In [3]:
from sklearn.cluster import KMeans
from sklearn.metrics import classification_report
import numpy as np
X = []
true_label = []
cluster_names = []
for key, val in embeddings.items():
    tl = value_dict[f"{key}.mp3"]
    if tl in ["female_feminine", "male_masculine"]:
        X.append(val)
        true_label.append(tl)
        if tl not in cluster_names:
            cluster_names.append(tl)
X = np.array(X)

kmeans = KMeans(n_clusters=2, random_state=0, n_init="auto").fit(X)
cluster_labels = kmeans.labels_

# not sure this is right--i think i want to be looking at cluster purity
print(classification_report(true_label, [cluster_names[l] for l in cluster_labels]))


                 precision    recall  f1-score   support

female_feminine       0.89      0.52      0.65       143
 male_masculine       0.32      0.79      0.46        42

       accuracy                           0.58       185
      macro avg       0.61      0.65      0.56       185
   weighted avg       0.76      0.58      0.61       185



In [12]:
confusion_matrix = np.zeros((2, 2))
buckets = ["female_feminine", "male_masculine"]
for idx, cl in enumerate(cluster_labels):
    confusion_matrix[buckets.index(true_label[idx])][cl] += 1
print(confusion_matrix)
purity_score = np.sum([np.max(r) for r in confusion_matrix])/len(cluster_labels)
print(purity_score)

[[74. 69.]
 [ 9. 33.]]
0.5783783783783784
